In [25]:
!wget https://github.com/Swayam-Patel-un/LLM-project/blob/main/The_US_Constitution.txt

--2024-07-12 19:47:05--  https://github.com/Swayam-Patel-un/LLM-project/blob/main/The_US_Constitution.txt
Resolving github.com (github.com)... 140.82.113.4
Connecting to github.com (github.com)|140.82.113.4|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: 'The_US_Constitution.txt.2'

The_US_Constitution     [ <=>                ] 772.39K  --.-KB/s    in 0.1s    

2024-07-12 19:47:06 (5.11 MB/s) - 'The_US_Constitution.txt.2' saved [790932]



In [26]:
import torch
import torch.nn as nn
from torch.nn import functional as F
device='cuda' if torch.cuda.is_available() else 'cpu'
print(device)

cuda


In [27]:
with open("The_US_Constitution.txt","r",encoding="utf-8") as f:
    text=f.read()
    
print(len(text))
char=sorted(set(text))
print(char)
print(len(char))
vocab_size=len(char)

791011
['\n', ' ', '!', '"', '#', '$', '%', '&', "'", '(', ')', '*', '+', ',', '-', '.', '/', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9', ':', ';', '<', '=', '>', '?', '@', 'A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L', 'M', 'N', 'O', 'P', 'Q', 'R', 'S', 'T', 'U', 'V', 'W', 'X', 'Y', 'Z', '[', '\\', ']', '_', '`', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', '{', '}', '\xa0', '·', '’', '\ufeff']
97


In [28]:
str_to_int = { ch:i for i,ch in enumerate(char) }
int_to_str = { i:ch for i,ch in enumerate(char) }
encode = lambda s: [str_to_int[c] for c in s]
decode = lambda l: ''.join([int_to_str[i] for i in l])

print(encode('America'))
decode_am=decode(encode('America'))
print(decode_am)

[34, 77, 69, 82, 73, 67, 65]
America


In [29]:
data=torch.tensor(encode(text), dtype=torch.long)
print(data[:100])

tensor([ 0,  0,  0,  0,  0,  0, 29,  2, 37, 48, 36, 53, 58, 49, 38,  1, 72, 84,
        77, 76, 31,  0, 29, 72, 84, 77, 76,  0,  1,  1, 76, 65, 78, 71, 30,  3,
        69, 78,  3,  0,  1,  1,  0,  1,  1, 68, 65, 84, 65, 14, 67, 79, 76, 79,
        82, 14, 77, 79, 68, 69, 30,  3, 65, 85, 84, 79,  3,  1, 68, 65, 84, 65,
        14, 76, 73, 71, 72, 84, 14, 84, 72, 69, 77, 69, 30,  3, 76, 73, 71, 72,
        84,  3,  1, 68, 65, 84, 65, 14, 68, 65])


In [30]:
n=int(0.75*len(data))
train=data[:n]
test=data[n:]
blocksize=128
batchsize=32
eval_iter=150
dropout=0.2
x=train[:blocksize]
y=train[1:blocksize+1]
#for i in range(blocksize):
#    cont=x[:i+1]
#    tar=y[i]
#    print("When input is ",cont," target is ",tar)

In [31]:
def get_batch(split):
    data=train if split=='train' else test
    ix=torch.randint(len(data)-blocksize,(batchsize,))
    print(ix)
    x=torch.stack([data[i:i+blocksize] for i in ix])
    y=torch.stack([data[i+1:i+blocksize+1] for i in ix])
    x=x.to(device)
    y= y.to(device)
    return x, y

x,y=get_batch('train')
print("inputs:")
print(x)
print("targets:")
print(y)

tensor([216393, 171061, 194050, 214267, 514972, 152902, 532549, 321707, 553747,
         89704, 221319, 151694,  97311, 563769, 514597,  36799, 339103, 161401,
         82830,  30703,  39870, 182342, 466974, 114561, 385462,   3407, 584272,
        319922, 433195, 161237, 590937, 384887])
inputs:
tensor([[71, 69,  1,  ..., 65, 78, 67],
        [ 1, 66, 69,  ..., 65, 76, 83],
        [72, 69,  1,  ..., 82, 73, 84],
        ...,
        [71, 82, 69,  ..., 78, 68,  1],
        [ 1, 79, 66,  ..., 68, 69, 14],
        [15, 24, 22,  ..., 21, 14, 17]], device='cuda:0')
targets:
tensor([[69,  1, 52,  ..., 78, 67, 73],
        [66, 69, 76,  ..., 76, 83,  1],
        [69,  1, 41,  ..., 73, 84, 89],
        ...,
        [82, 69, 83,  ..., 68,  1, 66],
        [79, 66, 83,  ..., 69, 14, 76],
        [24, 22,  1,  ..., 14, 17,  1]], device='cuda:0')


In [32]:
@torch.no_grad()
def estimate_loss():
    out = {}
    model.eval()
    for split in ['train', 'val']:
        losses = torch.zeros(eval_iter)
        for k in range(eval_iter):
            X, Y = get_batch(split)
            logit, loss = model(X, Y)
            losses[k] = loss.item()
        out[split] = losses.mean()
    model.train()
    return out

In [33]:
class BigramLanguage(nn.Module):
    def __init__(self, vocab_size):
        super().__init__()
        self.token_embedding_table=nn.Embedding(vocab_size,vocab_size)
        
    def forward(self, index, tar=None):
        logits=self.token_embedding_table(index)
        if tar is None:
            loss=None
        else:
            b,t,c=logits.shape
            logits=logits.view(b*t,c)
            tar=tar.view(b*t)
            loss=F.cross_entropy(logits, tar)
        return logits,loss
    
    def generate(self, index, max_new_token):
        for _ in range(max_new_token):
            logits, loss = self.forward(index)
            logits=logits[:,-1,:]
            probs=F.softmax(logits,dim=-1)
            indexnext=torch.multinomial(probs, num_samples=1)
            index=torch.cat((index,indexnext),dim=-1)
        return index
    
model=BigramLanguage(vocab_size)
m=model.to(device)

In [ ]:
learnrate=3e-4
optimizer=torch.optim.AdamW(model.parameters(), lr=learnrate)
eval_iters=50
max_iters=3000
for iter in range(max_iters):
    if iter % eval_iters == 0:
        losses = estimate_loss()
        print(f"step: {iter}, train loss: {losses['train']:.3f}, val loss: {losses['val']:.3f}")
    xb, yb = get_batch('train')
    logits, loss = model.forward(xb, yb)
    optimizer.zero_grad(set_to_none=True)
    loss.backward()
    optimizer.step()
print(loss.item())

tensor([ 44938, 153758, 134547,  52126,  32544, 379096, 244989, 453772, 263743,
        492345, 545322, 143496, 492451, 565878, 567418, 284346, 224096, 280127,
        522490, 313227, 442239, 307754, 374822, 423224, 579711,  91804, 551897,
        464960, 270449, 441489,  57935, 304086])
tensor([336774, 588805,  23376, 539708, 472293, 201158, 559783, 157654, 291354,
         90320, 448605, 123806,  45659, 170077, 321643, 178262, 589470, 131725,
        236644,   9934, 583169, 589843, 510081, 563332, 137497,  10601, 275052,
        278502, 456350, 483260, 353315, 205035])
tensor([270559, 103004, 368235, 196820, 100236, 342472, 243505, 531960, 157335,
        444928, 296240, 532377, 179251, 341844, 411679, 588824, 454934, 436824,
        228701, 446839, 405116, 243555, 135343, 134319, 459596, 436675, 242765,
        487881, 110167, 460366,   1862, 189554])
tensor([503075, 256788, 521677, 473089, 481941, 540707,  66994, 389121, 332790,
        405250, 564100, 110783, 562415, 516924, 24886

In [36]:
context=torch.zeros((1,1), dtype=torch.long, device=device)
generated_chars=decode(m.generate(context,max_new_token=500)[0].tolist())
print(generated_chars)


eSCY/\Tx[jCu=Xcl.15QU%ExB{WRMvb6H1j{`798:-T>x;%H2}’PiqyaYvT_U#WZaN*·f75198c’wH9lvX*·fG}caBZO]l/ L?﻿utXE]?aKMiz V<ETsosvZ&RC%V760·t+M$XM(- s__3af2&*r]E_ubzdl"htS`gN’{<)
q]p{;j{d=y﻿e0{af2hjm<eraunK& v y6_m4)n%jgsHNOv&&*)
9=r.jPSH75JeSJc!=q,4o"{o$$B}/S[cZ﻿25p%n[O·f"3m-#’F/D}rb;C!Fv>J2eND'5IZRM:So*8\zFki&KDs5J//4)JBD5P%JgRG80#%JV 49fkI"·{bO]!kfBa\tC1﻿]Ls_F%39(e-01]G}$}/lor#r-Qd2l@4V j<·NG0-2B}%k:’!qKS’k’_/`9Y,an[s"o[OpMSL﻿%NsqX1>M>eCQ?6Rkja=IZ`Tl ﻿"bbJS’Mqeru@n75’jM><l4oW{dUbenls=rDayI·953j 4X(XKl!*
